In [165]:
import geopy
import pickle
import json
import pymongo
from geopy.distance import vincenty
#import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
from slugify import slugify
import math
from numbers import Number

# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["bandsintown"]

# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'
#retrieve trip coords for each artist
dict_coords={}

import numpy as np
from matplotlib import pyplot as plt
DELTA_BETWEEN_DATES = 15,
MIN_DELTA_BETWEEN_DATES =4,
PLANE_DISTANCE = 1500,
MINIMUM_DATES = 5;

col = db[ 'selectedArtists' ]
newcol = db[ 'minedArtists' ];


In [212]:
from collections import defaultdict, OrderedDict
from operator import getitem 
from geopy.distance import geodesic
from datetime import timedelta
import math







artistList = [];
    
for artist in    col.find( {} ):
    artistList.append(artist["_id"])
    #print len(artist["gigs"]) 
    if len(artist["gigs"])<= MINIMUM_DATES:
        pass
    else:
        print "~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~"
        print artist["_id"]
        
        DICT_GIGS={}
        ARRAY_GIGS_DATETIME=[]
    
        #print artist["gigs"]
        for gig   in artist["gigs"]:
            DICT_GIGS[gig["datetime"]] = gig
            ARRAY_GIGS_DATETIME.append(gig["datetime"])
        #print "________"
    #print ARRAY_GIGS
        
        ORDERED_DICT_OF_GIGS = OrderedDict(sorted(DICT_GIGS.items(), 
           key = lambda x: getitem(x[1], 'datetime'))) 
        #print artist["_id"]
        #print ORDERED_DICT_OF_GIGS 
        totalKm = 0
        timeOnTour = 0;
        timeOffTour = 0;

        tours = [];
        tour = {};
        tour["gigs"] = [];

        singleGigs = [];
        toursCoords = {};
        idTour =0;
        tour["tourCoords"] =[];
        tourInProgress = False;
        dupl =0
        #print ARRAY_GIGS_DATETIME
        
        sorteddates = sorted(ARRAY_GIGS_DATETIME)
        #print sorteddates[0]
        #print sorteddates[1]
        #for (i= 0;i<=len(sorteddates-1),i++):
        i=0
        while(i<=(len( sorteddates)-2)): 
        
            
            #print index
            #print i
            #print sorteddates[i]
            #print sorteddates[i+1]
            GIG= ORDERED_DICT_OF_GIGS.get(sorteddates[i])
            NEXTGIG=ORDERED_DICT_OF_GIGS.get(sorteddates[i+1])
            #print GIG
            #print ORDERED_DICT_OF_GIGS.get(sorteddates[i+1])
            km=geodesic((GIG["venue"]['latitude'],GIG["venue"]['longitude']),(NEXTGIG["venue"]['latitude'],NEXTGIG["venue"]['longitude'])).km 
            #print km
            #nextgig=ORDERED_DICT_OF_GIGS[index]
            
            totalKm+=km
            #print totalKm
            GIG["distanceToNextGig"]= km
            GIG["timeToNextGig"]=(NEXTGIG["datetime"]-GIG["datetime"]).total_seconds()
            #print GIG["timeToNextGig"].total_seconds()
            #print timedelta(hours=4).total_seconds()
            #print str(GIG["timeToNextGig"].seconds),'TTNGG'
            #print "DELTA",timedelta(hours=4)
            #cd=timedelta(hours=4)
            #print cd
            if GIG["timeToNextGig"]<= timedelta(hours=4).total_seconds():
                dupl+=1
                
                pass
                
            
            
            elif (GIG["timeToNextGig"]> timedelta(hours=4).total_seconds())  and ( GIG["timeToNextGig"]<= timedelta(days=15).total_seconds()):
            #on tour
                if tourInProgress == False:
                  #  print "TOUR START"
                    tour={}
                    tour["gigs"]=[]
                    tour["tourCoords"]=[]
                
              #  print "TOUR CONTINUE 2"
                tour["gigs"].append(GIG)
                #print tour["gigs"]
                tourInProgress = True
                #print  tourInProgress
                #print GIG["timeToNextGig"]
                timeOnTour += GIG["timeToNextGig"]/3600
                tour["tourCoords"].append ([(GIG["venue"]['latitude'],GIG["venue"]['longitude'])])
            else:
                if tourInProgress == False:
                    singleGigs.append( GIG );
                 #   print "SG GIG"
                    tourInProgress = False
                else:
                   # print "TOUR END"
           
                    tour["distance"] = 0;
                    for g in tour["gigs"]:
                        tour['distance'] += g["distanceToNextGig"];
                    
                    tour["gigs"].append(GIG)
                    tour["tourCoords"].append ([(GIG["venue"]['latitude'],GIG["venue"]['longitude'])])
                    tour["nbGigs"] = len(tour["gigs"])
                    tourInProgress = False;
           #         print "TOUR"

                    tours.append( tour );
                timeOffTour += GIG["timeToNextGig"]/3600
            if ( i == len(sorteddates) - 2 ) :
                    #    print "HERE"
                        if tourInProgress==True:
                     #       print 'HERE2'
                            #print tour
                            tour["distance"] = 0;
                            for d in tour["gigs"] :
                                tour["distance"]  += d["distanceToNextGig"]
                            

                            tour["gigs"].append(NEXTGIG)
                            tour["nbGigs"] = len(tour["gigs"])
                            tour["tourCoords"].append ([(NEXTGIG["venue"]['latitude'],NEXTGIG["venue"]['longitude'])])
                            tourInProgress = False;
         #                   print "TOUR"
                            tours.append( tour )
                        else : 
                            singleGigs.append( NEXTGIG );
                            tourInProgress = False;
                            
            i+=1  
            
        nbDatesOnTour = 0
        #print "TOURS",tours
        
        for tour in tours:
            nbDatesOnTour += len(tour["gigs"])
            
            
        
            
        #print "TOUR",tour   
        #print len(tours)
        if len(tours) >1:
            
            meanTourLength = nbDatesOnTour / len(tours)
        #print "MEAN TOUR LENGTH",meanTourLength

             #    //ecart type
            sqEcarts = [];
            sumSqEcarts = 0;
            for toursq in tours:
                sqEcart= (len(toursq["gigs"]) - meanTourLength)**2
                sqEcarts.append(sqEcart)
                sumSqEcarts+=sqEcart

            ecartType = math.sqrt( sumSqEcarts / len(sqEcarts) );

#                // calculate total time
                
        totalTime = (ARRAY_GIGS_DATETIME[-1]-ARRAY_GIGS_DATETIME[0]).total_seconds()/3600

               #//TOUR DUTY CYCLE
        tourDutyCycle = timeOnTour / (totalTime);
            #    // console.log('tourDutyCycle = timeOnTour / totalTime:', tourDutyCycle * 100, '%' );

            #    // calcul du nombre moyen de dates / année
        meanOfGigsPerYear = len(artist["gigs"]) / (totalTime)
            #    // console.log('meanOfGigsByYear:', meanOfGigsPerYear);

            #   // calcul du délais moyen entre 2 concerts
        meanDelayBetweenGigs =(totalTime/24) / len(artist["gigs"])
     #           // console.log('meanDelayBetweenGigs:', meanDelayBetweenGigs, "days");

      #          //source: http://www.sightline.org/research/graphics/climate-co2bymode/
        co2Spent = totalKm / 3;
                #// console.log('co2 depense par membre du groupe (en kg) /premiere approx:', co2Spent);
        artist["name"] = artist["_id"]
        artist["slug"] = slugify( artist["_id"] )
        del  artist["_id"]  #remove id to allow auto mongo id
        artist["tours"] = tours
        artist["singleGigs"] = singleGigs
        artist["totalKm"] = totalKm
        artist["totalGigs"] = nbDatesOnTour + len(singleGigs)
        if len(tours) >1:
            artist["ecartType"] = ecartType
            
        artist["tourDutyCycle"] = tourDutyCycle
        artist["meanOfGigsPerYear"] = meanOfGigsPerYear
        artist["meanDelayBetweenGigs"] = meanDelayBetweenGigs
        artist["co2Spent"] = co2Spent
        #print "artist", artist
        print "PUSHING ARTIST ",artist["name"]
        print len(artist["gigs"])
        
        
        
        
        newcol.insert(artist)

print artistList[:20]

~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Adestria, Erra
PUSHING ARTIST   Adestria, Erra
13
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Joey Cape, Jon Snodgrass & Brian Wahlstrom
PUSHING ARTIST   Joey Cape, Jon Snodgrass & Brian Wahlstrom
14


/home/goonieb/gitrep/bandstour/venv/lib/python2.7/site-packages/ipykernel_launcher.py:215: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.


~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Novustory
PUSHING ARTIST   Novustory
23
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
 Phil Campbell and the Bastard Sons
PUSHING ARTIST   Phil Campbell and the Bastard Sons
42
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
!!!
PUSHING ARTIST  !!!
386
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Acoustic Africa"
PUSHING ARTIST  "Acoustic Africa"
25
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Scream The Prayer"
PUSHING ARTIST  "Scream The Prayer"
14
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
"Super DJ" Romeo
PUSHING ARTIST  "Super DJ" Romeo
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#1 Dads
PUSHING ARTIST  #1 Dads
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#PushYourDrumming
PUSHING ARTIST  #PushYourDrumming
8
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#PushYourDrumming/RolandVDrums
PUSHING ARTIST  #PushYourDrumming/RolandVDrums
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
$uicideboy$
PUSH

PUSHING ARTIST  2 Chainz
506
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Dudes with Acoustic Guitars
PUSHING ARTIST  2 Dudes with Acoustic Guitars
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Elements
PUSHING ARTIST  2 Elements
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 IN THE CHEST
PUSHING ARTIST  2 IN THE CHEST
17
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Many DJ's
PUSHING ARTIST  2 Many DJ's
338
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Men will move you
PUSHING ARTIST  2 Men will move you
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Mile Final
PUSHING ARTIST  2 Mile Final
155
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Rude
PUSHING ARTIST  2 Rude
17
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Sick Monkeys
PUSHING ARTIST  2 Sick Monkeys
24
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
2 Tone Lizard Kings
PUSHING ARTIST  2 Tone Lizard Kings
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
20 Reasons Taken
PUSHING 

59
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
40 oz. To Freedom
PUSHING ARTIST  40 oz. To Freedom
442
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
40oz Burrito: A Tribute to Sublime
PUSHING ARTIST  40oz Burrito: A Tribute to Sublime
16
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
42Radar
PUSHING ARTIST  42Radar
6
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
42nd Street
PUSHING ARTIST  42nd Street
287
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
45 Adapters
PUSHING ARTIST  45 Adapters
27
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
45 RPM
PUSHING ARTIST  45 RPM
45
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
45 rpm NY
PUSHING ARTIST  45 rpm NY
213
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
45RPM
PUSHING ARTIST  45RPM
14
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
45rpmny
PUSHING ARTIST  45rpmny
27
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
47SOUL
PUSHING ARTIST  47SOUL
44
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
4Dudes
PUSHING ARTIS

...

PUSHING ARTIST  settler
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
shEver
PUSHING ARTIST  shEver
71
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
shakespeare
PUSHING ARTIST  shakespeare
18
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
shoot the girl first
PUSHING ARTIST  shoot the girl first
23
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
shoto
PUSHING ARTIST  shoto
35
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
sicktanick
PUSHING ARTIST  sicktanick
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
silent
PUSHING ARTIST  silent
27
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
singer China Forbes
PUSHING ARTIST  singer China Forbes
259
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
singer China Forbes and special guests The von Trapps
PUSHING ARTIST  singer China Forbes and special guests The von Trapps
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
singer Storm Large
PUSHING ARTIST  singer Storm Large
106
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  the Coral Reefer Band
117
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Cordovas
PUSHING ARTIST  the Cordovas
219
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Courtesans
PUSHING ARTIST  the Courtesans
41
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Cryptics
PUSHING ARTIST  the Cryptics
68
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Cured
PUSHING ARTIST  the Cured
6
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Deadlies
PUSHING ARTIST  the Deadlies
20
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Deadmen
PUSHING ARTIST  the Deadmen
31
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Deer
PUSHING ARTIST  the Deer
149
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Deloreans
PUSHING ARTIST  the Deloreans
32
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Dewars
PUSHING ARTIST  the Dewars
9
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Dirty Diamond
PUSHING ARTIST  the Dirty Diamond
44
~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  the Shady Horns
49
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shag Rats
PUSHING ARTIST  the Shag Rats
21
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shills
PUSHING ARTIST  the Shills
65
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Ship
PUSHING ARTIST  the Ship
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Shrine
PUSHING ARTIST  the Shrine
71
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Silver Bullet Band
PUSHING ARTIST  the Silver Bullet Band
31
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Skeleton Crew
PUSHING ARTIST  the Skeleton Crew
6
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Skyline
PUSHING ARTIST  the Skyline
7
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Sleeper
PUSHING ARTIST  the Sleeper
63
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Small Glories
PUSHING ARTIST  the Small Glories
31
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
the Snips
PUSHING ARTIST  the Snips
28
~~~~~~~~~~~

PUSHING ARTIST  w/ Lee Bains III & The Glory Fires
8
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
w/ The Devil Makes Three
PUSHING ARTIST  w/ The Devil Makes Three
17
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
w/ This Or The Apocalypse, Ice Nine Kills
PUSHING ARTIST  w/ This Or The Apocalypse, Ice Nine Kills
6
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
w/Billy Masters on guitar
PUSHING ARTIST  w/Billy Masters on guitar
8
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
waFF
PUSHING ARTIST  waFF
262
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
waldden
PUSHING ARTIST  waldden
69
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wankelmut
PUSHING ARTIST  wankelmut
190
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wavelengths
PUSHING ARTIST  wavelengths
13
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
wax wings
PUSHING ARTIST  wax wings
10
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
waxworks
PUSHING ARTIST  waxworks
21
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

PUSHING ARTIST  Сплин
12
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
أم كلثوم
PUSHING ARTIST  أم كلثوم
8
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
श्रेया घोषाल
PUSHING ARTIST  श्रेया घोषाल
52
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
सोनू निगम
PUSHING ARTIST  सोनू निगम
45
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
ᵀᴴᴱ ᴼᴿᴵᴳᴵᴻᴬᴸ Funky Monkey
PUSHING ARTIST  ᵀᴴᴱ ᴼᴿᴵᴳᴵᴻᴬᴸ Funky Monkey
203
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
デザート
PUSHING ARTIST  デザート
22
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
久石譲
PUSHING ARTIST  久石譲
6
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
任賢齊
PUSHING ARTIST  任賢齊
7
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
王羽佳
PUSHING ARTIST  王羽佳
84
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
郎朗
PUSHING ARTIST  郎朗
54
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
陳光榮
PUSHING ARTIST  陳光榮
215
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
鼓童
PUSHING ARTIST  鼓童
76
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
비
PUSHING